In [4]:
## Import Libraries
import os
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import seaborn as sns
import warnings

import plotly.express as px
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot, plot
from plotly.subplots import make_subplots

from IPython.core.display import HTML
from IPython.display import Image, Audio, Video

%matplotlib inline
warnings.filterwarnings("ignore")

In [5]:
def my_cut (x, bins, lower_infinite=False, upper_infinite=False, **kwargs):
    # Quick passthru if no infinite bounds
    if not lower_infinite and not upper_infinite:
        return pd.cut(x, bins, **kwargs)

    # Setup
    num_labels      = len(bins) - 1
    include_lowest  = kwargs.get("include_lowest", False)
    right           = kwargs.get("right", True)

    # Prepend/Append infinities where indiciated
    bins_final = bins.copy()
    if upper_infinite:
        bins_final.insert(len(bins),float("inf"))
        num_labels += 1
    if lower_infinite:
        bins_final.insert(0,float("-inf"))
        num_labels += 1

    # Decide all boundary symbols based on traditional cut() parameters
    symbol_lower  = "<=" if include_lowest and right else "<"
    left_bracket  = "(" if right else "["
    right_bracket = "]" if right else ")"
    symbol_upper  = ">" if right else ">="

    # Inner function reused in multiple clauses for labeling
    def make_label(i, lb=left_bracket, rb=right_bracket):
        return "{0} - {1}".format(bins_final[i], bins_final[i+1])
    
   # Create custom labels
    labels=[]
    for i in range(0,num_labels):
        new_label = None

        if i == 0:
            if lower_infinite:
                new_label = "{0} {1}".format(symbol_lower, bins_final[i+1])
            elif include_lowest:
                new_label = make_label(i, lb="[")
            else:
                new_label = make_label(i)
        elif upper_infinite and i == (num_labels - 1):
            new_label = "{0} {1}".format(symbol_upper, bins_final[i])
        else:
            new_label = make_label(i)

        labels.append(new_label)

    # Pass thru to pandas cut()
    return pd.cut(x, bins_final, labels=labels, **kwargs)

In [6]:
# open filel with the raw data
file = open(r"C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\trending.json", encoding="utf8")

raw_data = json.load(file)
file.close()

# select only the list with the video data
trending_videos_list = raw_data['collector']
print(json.dumps(trending_videos_list[15], indent=4, sort_keys=True))

{
    "authorMeta": {
        "avatar": "https://p77-sign-sg.tiktokcdn.com/tos-maliva-avt-0068/ce5595b5c4874a234d0e41feec9b4ef9~c5_1080x1080.jpeg?x-expires=1608649200&x-signature=HXQeWxkqcbcR2JEz9JRdZWOhJ%2Fw%3D",
        "id": "6563548229581422598",
        "name": "jhullyduarte",
        "nickName": "Jhully Duarte",
        "secUid": "MS4wLjABAAAAByNqbJCtA9PfwY1ICwGomesu7URs6GhushkQeWleqhqsTSRmCKKi1GpUXOWabnbI",
        "signature": "\ud83e\udd2a\ud83e\udd2a",
        "verified": false
    },
    "commentCount": 267,
    "covers": {
        "default": "https://p16-sign-sg.tiktokcdn.com/obj/tos-maliva-p-0068/6416d73acd5a47c0bb04c0982e4b973e?x-expires=1608584400&x-signature=qa5fI0p5HrD71YMq70ImAirJtzI%3D",
        "dynamic": "https://p16-sign-sg.tiktokcdn.com/obj/tos-maliva-p-0068/b45558f5231340cdbf9f34f5574cc98c_1608239182?x-expires=1608584400&x-signature=IWs7ofM62Z2%2FcvyxJhpYLZowafM%3D",
        "origin": "https://p16-sign-sg.tiktokcdn.com/obj/tos-maliva-p-0068/c137bcc58fcc4798b3052

In [35]:
# create a DataFrame of the data
df = pd.DataFrame(trending_videos_list)
df

id                                               text  \
0    6907228749016714497                                  Confidence went 📈   
1    6875468410612993286  Quiet Zone... follow me on insta: joeysofo. Co...   
2    6898699405898059010  Iphone bend test🤗 #tiktok #viral #fyp #iphone ...   
3    6902819837345533186                                                      
4    6905635666588192002                           小技です👟✨#tiktok教室#tutorial   
..                   ...                                                ...   
995  6877191692341054721                                #foryou #foryoupage   
996  6908069845825359109  Stop eating 💩 #gttfg #gotothegym #swolefam #nu...   
997  6883484287434378497                            #fy #foryoupage #foryou   
998  6898721943978036481                     regretss 📈 #fyp #foryou #curls   
999  6899116261746281730  The collab you didn’t know you needed, myself ...   

     createTime                                         authorMeta  \
0    1608214517  {'id': '6825540583826768902', 'secUid': 'MS4wL...   
1    1600819763  {'id': '6729292817489986566', 'secUid': 'MS4wL...   
2    1606228625  {'id': '6791901371429913601', 'secUid': 'MS4wL...   
3    1607187987  {'id': '6574079584262094854', 'secUid': 'MS4wL...   
4    1607843600  {'id': '6586854399372394498', 'secUid': 'MS4wL...   
..          ...                                                ...   
995  1601220970  {'id': '6788447048146600965', 'secUid': 'MS4wL...   
996  1608410366  {'id': '6718786745917506565', 'secUid': 'MS4wL...   
997  1602686079  {'id': '6792309272296129541', 'secUid': 'MS4wL...   
998  1606233872  {'id': '69570057726554112', 'secUid': 'MS4wLjA...   
999  1606325682  {'id': '6798143079889470469', 'secUid': 'MS4wL...   

                                             musicMeta  \
0    {'musicId': '6790057285814061057', 'musicName'...   
1    {'musicId': '6678927595137977094', 'musicName'...   
2    {'musicId': '6881287666340481026', 'musicName'...   
3    {'musicId': '6881107586830076678', 'musicName'...   
4    {'musicId': '6649693417590754053', 'musicName'...   
..                                                 ...   
995  {'musicId': '6843814375833291525', 'musicName'...   
996  {'musicId': '6908069867644013318', 'musicName'...   
997  {'musicId': '6863497148655225605', 'musicName'...   
998  {'musicId': '6807084883974851333', 'musicName'...   
999  {'musicId': '57419989', 'musicName': 'Potentia...   

                                                covers  \
0    {'default': 'https://p16-sign-sg.tiktokcdn.com...   
1    {'default': 'https://p16-sign-sg.tiktokcdn.com...   
2    {'default': 'https://p16-sign-sg.tiktokcdn.com...   
3    {'default': 'https://p16-sign-sg.tiktokcdn.com...   
4    {'default': 'https://p16-sign-sg.tiktokcdn.com...   
..                                                 ...   
995  {'default': 'https://p16-sign-sg.tiktokcdn.com...   
996  {'default': 'https://p16-sign-sg.tiktokcdn.com...   
997  {'default': 'https://p16-sign-sg.tiktokcdn.com...   
998  {'default': 'https://p16-sign-sg.tiktokcdn.com...   
999  {'default': 'https://p16-sign-sg.tiktokcdn.com...   

                                           webVideoUrl  \
0    https://www.tiktok.com/@ninakleij/video/690722...   
1    https://www.tiktok.com/@joeysofo/video/6875468...   
2    https://www.tiktok.com/@jackeyephone/video/689...   
3    https://www.tiktok.com/@naomivaneeren/video/69...   
4    https://www.tiktok.com/@io.dreamer_mk/video/69...   
..                                                 ...   
995  https://www.tiktok.com/@artistmiranda/video/68...   
996  https://www.tiktok.com/@papaswolio/video/69080...   
997  https://www.tiktok.com/@sanaelfarah/video/6883...   
998  https://www.tiktok.com/@safae.kx/video/6898721...   
999  https://www.tiktok.com/@erinwilliams_1/video/6...   

                                              videoUrl videoUrlNoWaterMark  \
0    https://v77.tiktokcdn.com/ed1f811617d7b5e18b8d...         

In [8]:
df = df.explode('hashtags').explode('mentions')
df = df.drop(['authorMeta', 'musicMeta', 'covers', 'videoMeta', 'hashtags'], axis=1)
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5693 entries, 0 to 999
Data columns (total 12 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   id                   5693 non-null   object
 1   text                 5693 non-null   object
 2   createTime           5693 non-null   int64 
 3   webVideoUrl          5693 non-null   object
 4   videoUrl             5693 non-null   object
 5   videoUrlNoWaterMark  5693 non-null   object
 6   diggCount            5693 non-null   int64 
 7   shareCount           5693 non-null   int64 
 8   playCount            5693 non-null   int64 
 9   commentCount         5693 non-null   int64 
 10  downloaded           5693 non-null   bool  
 11  mentions             1316 non-null   object
dtypes: bool(1), int64(5), object(6)
memory usage: 539.3+ KB


In [9]:
# make a function
def object_to_columns(dfRow, **kwargs):
    """Function to expand cells containing dictionaries, to columns"""
    for column, prefix in kwargs.items():
        if isinstance(dfRow[column], dict):
            for key, value in dfRow[column].items():
                columnName = '{}.{}'.format(prefix, key)
                dfRow[columnName] = value
    return dfRow

#df = df.apply(object_to_columns, 
 ##                          musicMeta='musicMeta',
   #                         covers='cover',
    #                        videoMeta='videoMeta',
     #                       hashtags='hashtag', axis = 1)

# Remove the original columns containing the dictionaries
df = pd.json_normalize(trending_videos_list)
df = df.explode('hashtags').explode('mentions').to_json(orient='records')
parsed = json.loads(df)
df = pd.json_normalize(parsed)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5693 entries, 0 to 5692
Data columns (total 38 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       5693 non-null   object 
 1   text                     5693 non-null   object 
 2   createTime               5693 non-null   int64  
 3   webVideoUrl              5693 non-null   object 
 4   videoUrl                 5693 non-null   object 
 5   videoUrlNoWaterMark      5693 non-null   object 
 6   diggCount                5693 non-null   int64  
 7   shareCount               5693 non-null   int64  
 8   playCount                5693 non-null   int64  
 9   commentCount             5693 non-null   int64  
 10  downloaded               5693 non-null   bool   
 11  mentions                 1316 non-null   object 
 12  hashtags                 0 non-null      float64
 13  authorMeta.id            5693 non-null   object 
 14  authorMeta.secUid       

In [10]:
# Get unique rows from dataset
df_unique_videos = df.drop_duplicates(subset='id', keep="first")
df_unique_music = df.drop_duplicates(subset='musicMeta.musicId', keep="first")
df_unique_authors = df.drop_duplicates(subset='authorMeta.id', keep="first")

# Show amount of rows per dataset
{
    'df_tiktok_dataset': df.shape,
    'df_unique_videos': df_unique_videos.shape,
    'df_unique_music': df_unique_music.shape,
    'df_unique_authors': df_unique_authors.shape
}

{'df_tiktok_dataset': (5693, 38),
 'df_unique_videos': (1000, 38),
 'df_unique_music': (907, 38),
 'df_unique_authors': (802, 38)}

In [11]:
df.describe()

createTime     diggCount     shareCount     playCount   commentCount  \
count  5.693000e+03  5.693000e+03    5693.000000  5.693000e+03    5693.000000   
mean   1.604877e+09  5.630986e+04    1481.563323  6.062278e+05     701.559283   
std    2.282009e+06  4.927927e+05    8580.033748  4.554259e+06    8671.442272   
min    1.600785e+09  1.300000e+01       0.000000  4.650000e+02       0.000000   
25%    1.602862e+09  3.090000e+03      20.000000  4.710000e+04      51.000000   
50%    1.604961e+09  7.320000e+03      82.000000  8.190000e+04     123.000000   
75%    1.606932e+09  2.140000e+04     388.000000  1.973000e+05     370.000000   
max    1.608521e+09  3.100000e+07  220100.000000  2.508000e+08  625700.000000   

       hashtags  videoMeta.height  videoMeta.width  videoMeta.duration  
count       0.0       5693.000000      5693.000000         5693.000000  
mean        NaN        977.729492       579.945547           20.568066  
std         NaN        119.002955        78.260349           14.964944  
min         NaN        352.000000       240.000000            4.000000  
25%         NaN        960.000000       576.000000           10.000000  
50%         NaN       1024.000000       576.000000           15.000000  
75%         NaN       1024.000000       576.000000           25.000000  
max         NaN       1248.000000      1248.000000           60.000000

Data Analysis for Likes n comment Data

In [12]:
# set bucket ranges
buckets = list(range(0, 105000, 5000)) # range like around 

likes = df_unique_videos.groupby(my_cut(df_unique_videos['diggCount'], buckets, upper_infinite=True)).diggCount.count()
comments = df_unique_videos.groupby(my_cut(df_unique_videos['commentCount'], buckets, upper_infinite=True)).diggCount.count()

# Transform from series to dataframe with some small modifications
likes = likes.rename('likes').to_frame().reset_index()
comments = comments.rename('comments').to_frame().reset_index()

# create subplots, two rows and 1 column each row
fig = make_subplots(2, 1, subplot_titles=("Distribution of Likes", "Distribution of Comments"))

# First plot
fig.add_trace(
    go.Bar(y = likes['diggCount'], 
           x = likes['likes'], 
           name="Likes",
           text = likes['likes'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='rgb(162, 210, 255)'
    ),
    row=1,col=1
)

# second plot
fig.add_trace(
    go.Bar(y = comments['commentCount'], 
           x = comments['comments'], 
           name="Comments",
           text = comments['comments'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='black'
    ),
    row=2,col=1
)

fig.update_layout(uniformtext_minsize=8,
                  uniformtext_mode='hide',
                  title_text="Multiple Subplots with Titles",
                  height=1200,
                  template='plotly_white',
                  margin=go.layout.Margin(
                      l=130, r=5, b=5, t=100, pad=10
                  ))

fig.update_xaxes(title_text='Videos')
fig.update_yaxes(title_text='Likes', col=1, row=1, automargin=False)
fig.update_yaxes(title_text='Comments', col=1, row=2, automargin=False)
fig.show(config={'displayModeBar': False})

In [13]:
# Focus on dataset from 0 till 50.000 likes
df_videos_users_focus = df_unique_videos[df_unique_videos['diggCount'] <= 50000] # count of dataset likes

# Create a scatter plot with a trendline
fig = px.scatter(df_videos_users_focus, trendline='ols',
                 x='diggCount',
                 y='commentCount',
                 labels={
                     'diggCount':'Likes',
                     'commentCount':'Comments'
                 },
                 log_y=True,
                 trendline_color_override="#ff7096",
                 template='plotly_white')

fig.update_traces(marker=dict(
    color='#4cc9f0',
    opacity=0.6
))
fig.show()

Popular Hashtags

In [14]:
# Create a DataFrame of the data
df_hashtags = pd.DataFrame(trending_videos_list) # containing data from trending video list into dataframe

# Let's expand the hashtag cell containing dictionaries to columns
df_hashtags = df_hashtags.explode('hashtags')

# Expand certain cells containing dictionaries to columns
df_hashtags = df_hashtags.apply(object_to_columns, hashtags='hashtag', axis=1)
hashtags = df_hashtags[['hashtag.name']].copy().dropna()
hashtags.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5330 entries, 2 to 999
Data columns (total 1 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   hashtag.name  5330 non-null   object
dtypes: object(1)
memory usage: 83.3+ KB


In [15]:
# Add column with default value
hashtags['count'] = 1

# Count all hashtags, group and replace the count column value with the sum
hashtags = hashtags.groupby(['hashtag.name'])['count'].count().reset_index()

# Sort by most popular hashtags and keep the top 15
hashtags = hashtags.sort_values(by='count', ascending=False)[:15]

# Create a Pie Chart with all values
fig = go.Figure(data=[go.Pie(
    labels=hashtags['hashtag.name'],
    values=hashtags['count'],
    textinfo='label+percent',
    insidetextorientation='radial'
)],
# Set colours for layout
layout={'colorway': ["#f72585","#b5179e",
                     "#7209b7","#560bad",
                     "#480ca8","#3a0ca3",
                     "#3f37c9","#4361ee",
                     "#4895ef","#4cc9f0"]})

fig.update_layout(title_text="Tiktok trending analytics",
                  height=700,
                  width=800,
                  margin=go.layout.Margin(
                      l=130, r=5, b=5, t=100, pad=10))
fig.show(config={'displayModeBar': False})

Enrich Data

In [16]:
df_audd_music = pd.read_csv('audd_music.csv', index_col='id')
df_audd_music_apple = pd.read_csv('audd_music_apple_music.csv')
df_audd_music_spotify = pd.read_csv('audd_music_spotify_music.csv')
df_audd_music_spotify_artists = pd.read_csv('audd_music_spotify_music_artists.csv')

In [17]:
# The current version of the dataset contains duplicated rows, remove them
df_audd_music = df_audd_music.drop_duplicates()

# Add prefic to this datasetm before merging
df_audd_music = df_audd_music.add_prefix('_audd_music.')
df_audd_music.shape

(471, 9)

In [18]:
# create a dataframe of the data sort from trending videos list
df_tiktok_music = pd.DataFrame(trending_videos_list)

# expand certain cells containing dictionaries to columns
df_tiktok_music = df_tiktok_music.apply(object_to_columns, musicMeta='musicMeta', axis=1)   

# Convert the columns dtype to int64 so we can merge
df_tiktok_music['musicMeta.musicId'] = df_tiktok_music['musicMeta.musicId'].astype('int64')
df_tiktok_music.shape

(1000, 25)

In [19]:
df_tiktok_audd_music = df_tiktok_music.merge(df_audd_music,
                                             how='left',
                                             right_on='id',
                                             left_on='musicMeta.musicId')
df_tiktok_audd_music.shape

(1000, 34)

Original sounds examples

In [20]:
df_tiktok_audd_music = df_tiktok_audd_music[(df_tiktok_audd_music['musicMeta.musicName'] == 'origineel geluid') &
                                            df_tiktok_audd_music['_audd_music.artist'].notna()]
df_tiktok_audd_music

id                                               text  \
6    6895303013867539713                                              Oh no   
150  6889831681469975810  Fishikta ameley❤️#eritreanmusic#habeshatiktok#...   
202  6883565215552654593  we surprised my mom with her dream car for her...   
242  6876145412105899265  De trend na doen toch 🙃🙃 🏐🏐🏐#volleybal #traini...   
297  6884691950478298370                                      🦋🦋🦋🦋🦋vlinders   
298  6888218363923942657                            Legend dat ie dat durft   
334  6898350532415540482  #soundwavestattoo #spotifytattoo #tattoo #amst...   
347  6876860979787959554   #fy #voorjou #foryou #fördich #covid #quarantine   
348  6895338661622123777  Follow the chain #bottle #viral #bottleflipcha...   
487  6903854177072499969  Ruut doet mee aan de hype 😂 #foryou #fyp #voor...   
498  6900492821862599938  Wie herinnert zich dit nummer nog ? #jumpstyle...   
538  6900478499933408513  Factory days #redbull #redbullracing #f1 #form...   
543  6898642858484567297  Lewis was not amused by Max back then 🤭 #hamil...   
568  6899736406495677697  blijf vechten voor onze vrijheid! #vuurwerkver...   
614  6903898067490163969  So naar @royalistiq Sws! Uitbrengen🔥👀 #fy #fyp...   
669  6905063271129287938  Kan er niks aan doen #voorjoupagina #fyp #fitness   
715  6906649897869659394                                                      
757  6904236597529595138  Haring ver van t’ mes #hollandsroem #haring #h...   
762  6896943341666127105  #drag #dragqueen #draqmakeover #dragqueentrans...   
849  6891693185693797634  Tja verschil moet er zijn #boyfriend #relation...   
866  6898022622110436609  Best Duo Of With McLaren ‘19 #f1 #formula1 #fy...   
903  6908311912941931777  Zo kan het ook jongens #coronaproof #balkonfee...   
905  6905326071026109697                            #duet met @ryan.perdaan   
942  6889162600534330625  DIY wallart. For tutorial video instagram: @gu...   
994  6879000638458449153  😜😜😜#magikbijjouslapen#love#nederland#fyp#foryo...   

     createTime                                         authorMeta  \
6    1605437840  {'id': '6879814870579512326', 'secUid': 'MS4wL...   
150  1604163946  {'id': '6775997579706008582', 'secUid': 'MS4wL...   
202  1602704922  {'id': '6781188628154942469', 'secUid': 'MS4wL...   
242  1600977365  {'id': '6725806948447060997', 'secUid': 'MS4wL...   
297  1602967260  {'id': '56906553353601024', 'secUid': 'MS4wLjA...   
298  1603788318  {'id': '6592928888640536582', 'secUid': 'MS4wL...   
334  1606147396  {'id': '6789291619143123974', 'secUid': 'MS4wL...   
347  1601143970  {'id': '6811941079287743494', 'secUid': 'MS4wL...   
348  1605446140  {'id': '6843492627725059078', 'secUid': 'MS4wL...   
487  1607428817  {'id': '6652957483734974469', 'secUid': 'MS4wL...   
498  1606646187  {'id': '6817606224172090374', 'secUid': 'MS4wL...   
538  1606642852  {'id': '6892683353885459457', 'secUid': 'MS4wL...   
543  1606215459  {'id': '6732359639461708806', 'secUid': 'MS4wL...   
568  1606470071  {'id': '90675406688632832', 'secUid': 'MS4wLjA...   
614  1607439032  {'id': '6812891539712754694', 'secUid': 'MS4wL...   
669  1607710329  {'id': '6722378617680118790', 'secUid': 'MS4wL...   
715  1608079748  {'id': '6768484239110800389', 'secUid': 'MS4wL...   
757  1607517852  {'id': '6845623072784778245', 'secUid': 'MS4wL...   
762  1605819760  {'id': '6896932285107602434', 'secUid': 'MS4wL...   
849  1604597362  {'id': '6798246867837142022', 'secUid': 'MS4wL...   
866  1606071049  {'id': '6892683353885459457', 'secUid': 'MS4wL...   
903  1608466711  {'id': '17992268', 'secUid': 'MS4wLjABAAAAYGyS...   
905  1607771515  {'id': '6852789418405135366', 'secUid': 'MS4wL...   
942  1604008165  {'id': '6866726949495079941', 'secUid': 'MS4wL...   
994  1601642148  {'id': '6818871838464050181', 'secUid': 'MS4wL...   

                                             musicMeta  \
6    {'musicId': '6893870343761496834', 'musicName'...   
150  {'musicId': '688138238431

In [21]:
import numpy as np

tiktok_set_new = np.array(df_tiktok_audd_music['hashtags'])
pd.json_normalize(tiktok_set_new)

0   \
0                                                None   
1   {'id': '66390205', 'name': 'eritreanmusic', 't...   
2   {'id': '15379', 'name': 'surprise', 'title': '...   
3   {'id': '335226', 'name': 'volleybal', 'title':...   
4                                                None   
5                                                None   
6   {'id': '1651372024079366', 'name': 'soundwaves...   
7   {'id': '153828', 'name': 'fy', 'title': '', 'c...   
8   {'id': '82512', 'name': 'bottle', 'title': '',...   
9   {'id': '42164', 'name': 'foryou', 'title': '',...   
10  {'id': '300674', 'name': 'jumpstyle', 'title':...   
11  {'id': '12573', 'name': 'redbull', 'title': ''...   
12  {'id': '134122', 'name': 'hamilton', 'title': ...   
13  {'id': '1654160921584645', 'name': 'vuurwerkve...   
14  {'id': '153828', 'name': 'fy', 'title': '', 'c...   
15  {'id': '1603519477711878', 'name': 'voorjoupag...   
16                                               None   
17  {'id': '1685604573794306', 'name': 'hollandsro...   
18  {'id': '11059', 'name': 'drag', 'title': '', '...   
19  {'id': '5849', 'name': 'boyfriend', 'title': '...   
20  {'id': '16520', 'name': 'f1', 'title': '', 'co...   
21  {'id': '1660606986519557', 'name': 'coronaproo...   
22  {'id': '30496', 'name': 'duet', 'title': 'Use ...   
23  {'id': '18121', 'name': 'diy', 'title': 'Do it...   
24  {'id': '1671999227560965', 'name': 'magikbijjo...   

                                                   1   \
0                                                None   
1   {'id': '1638738865659910', 'name': 'habeshatik...   
2   {'id': '10007', 'name': 'birthday', 'title': '...   
3   {'id': '12621', 'name': 'training', 'title': '...   
4                                                None   
5                                                None   
6   {'id': '1677956684867586', 'name': 'spotifytat...   
7   {'id': '6830763', 'name': 'voorjou', 'title': ...   
8   {'id': '20884', 'name': 'viral', 'title': '', ...   
9   {'id': '229207', 'name': 'fyp', 'title': '', '...   
10  {'id': '1406357', 'name': '2007', 'title': '',...   
11  {'id': '2012369', 'name': 'redbullracing', 'ti...   
12  {'id': '16199277', 'name': 'verstappen', 'titl...   
13  {'id': '1675301822296070', 'name': 'mondkapjes...   
14  {'id': '229207', 'name': 'fyp', 'title': '', '...   
15  {'id': '229207', 'name': 'fyp', 'title': '', '...   
16                                               None   
17  {'id': '9287639', 'name': 'haring', 'title': '...   
18  {'id': '17364', 'name': 'dragqueen', 'title': ...   
19  {'id': '14328', 'name': 'relationship', 'title...   
20  {'id': '402512', 'name': 'formula1', 'title': ...   
21  {'id': '1666424733495301', 'name': 'balkonfees...   
22                                               None   
23  {'id': '456806', 'name': 'tutorials', 'title':...   
24  {'id': '4231', 'name': 'love', 'title': '', 'c...   

                                                   2   \
0                                                None   
1   {'id': '35322719', 'name': 'eritreangirl', 'ti...   
2   {'id': '6057', 'name': 'mom', 'title': '', 'co...   
3   {'id': '1741293', 'name': 'laat', 'title': '',...   
4                                                None   
5                                                None   
6   {'id': '17922', 'name': 'tattoo', 'title': '',...   
7   {'id': '42164', 'name': 'foryou', 'title': '',...   
8   {'id': '15065490', 'name': 'bottleflipchalleng...   
9   {'id': '6830763', 'name': 'voorjou', 'title': ...   
10  {'id': '6830763', 'name': 'voorjou', 'title': ...   
11  {'id': '16520', 'name': 'f1', 'title': '', 'co...   
12  {'id': '21488046', 'name': 'bahraingp', 'title...   
13  {'id': '2147080', 'name': 'langefrans', 'title...   
14  {'id': '6830763', 'name': 'voorjou', 'title': ...   
15  {'id': '9261', 'name': 'fitness', 'title': 'De...   
16                                               None   
17  {'id': '18347', 'name': 'holland', 'title': ''...   
18

In [22]:
videoUrl = df_tiktok_audd_music.iloc[2]['musicMeta.playUrl']
url = df_tiktok_audd_music.iloc[2]['webVideoUrl']
print('Url to full video:', url)
print('Sound recognized by Audd:', df_tiktok_audd_music.iloc[2]['_audd_music.artist'],
      '-', df_tiktok_audd_music.iloc[2]['_audd_music.title'])
print('original sounds:')
Audio(df_tiktok_audd_music.iloc[2]['musicMeta.playUrl'])

Url to full video: https://www.tiktok.com/@curlsnclouds/video/6883565215552654593
Sound recognized by Audd: Ritt Momney - Put Your Records On
original sounds:


Contoh mengambil data baris ke -6 

In [23]:
# Mengambil data baris ke-6 dari df_tiktok_audd_music
row6 = df_tiktok_audd_music.iloc[5]
videoUrl = row6['musicMeta.playUrl']
url = row6['webVideoUrl']
print('Url to full video:', url)
print('Sound recognized by Audd:', row6['_audd_music.artist'], '-', row6['_audd_music.title'])
print('original sounds:')
Audio(row6['musicMeta.playUrl'])

Url to full video: https://www.tiktok.com/@waaromjaron/video/6888218363923942657
Sound recognized by Audd: Fernando Velázquez - The Monster Wakes Up
original sounds:


In [24]:
bucks = list(range(0, 250000, 10000))

likes_most = df_unique_videos.groupby(my_cut(df_unique_videos['diggCount'], bucks, upper_infinite=True)).diggCount.count()
comments_most = df_unique_videos.groupby(my_cut(df_unique_videos['commentCount'], bucks, upper_infinite=True)).diggCount.count()

# Transform to small modifications data row n columns
likes_most = likes_most.rename('likes_most').to_frame().reset_index()
comments_most = comments_most.rename('comments_most').to_frame().reset_index()

# make a plot

fig = make_subplots(2, 1, subplot_titles=("Distribution of most likes", "Distribution of most comments"))

# First plot
fig.add_trace(
    go.Bar(y = likes_most['diggCount'], 
           x = likes_most['likes_most'], 
           name="Likes",
           text = likes_most['likes_most'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='#f82342'
    ),
    row=1,col=1
)

# second plot
fig.add_trace(
    go.Bar(y = comments_most['commentCount'], 
           x = comments_most['comments_most'], 
           name="Comments",
           text = comments_most['comments_most'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='green'
    ),
    row=2,col=1
)

fig.update_layout(uniformtext_minsize=8,
                  uniformtext_mode='hide',
                  title_text="Multiple Subplots with Titles",
                  height=1200,
                  template='plotly_white',
                  margin=go.layout.Margin(
                      l=130, r=5, b=5, t=100, pad=10
                  ))

fig.update_xaxes(title_text='Videos')
fig.update_yaxes(title_text='Likes', col=1, row=1, automargin=False)
fig.update_yaxes(title_text='Comments', col=1, row=2, automargin=False)
fig.show(config={'displayModeBar': False})

In [25]:
plot_videos = df_unique_videos[df_unique_videos['diggCount'] <= 200000]

fig = px.scatter(plot_videos, trendline='ols',
                 x='diggCount',
                 y='commentCount',
                 labels={
                     'diggCount':'Likes',
                     'commentCount':'Comments'
                 },
                 log_y=True,
                 trendline_color_override="red",
                 template='plotly_white')

fig.update_traces(marker=dict(
    color='#008000',
    opacity=0.6
))
fig.show()

In [26]:
min_likes = 20000
max_likes = 30000

# we assume the algorithm videos must be in range <= 30000 likes instead.
# make a boolean filter for discovering video in the range
filter_likes = (df_unique_videos['diggCount'] >= min_likes) & (df_unique_videos['diggCount'] <= max_likes)

# apply filter into DataFrame and get tiktok user randomly
df_filter = df_unique_videos[filter_likes].sample(n=5)

print(f"Video through most likes is found between {min_likes} and {max_likes}")
df_filter

Video through most likes is found between 20000 and 30000


id                                               text  \
3060  6900478499933408513  Factory days #redbull #redbullracing #f1 #form...   
4512  6877869447999245569  Let’s get those boulder shoulders fellas 😈 #bo...   
5535  6904238654751870209  Рукожопы#встилеRIO #рекомендации #рек #стройка...   
2144  6907464609116982529  #kesfet #turkish #asianmakeup #foryou #viral #...   
1531  6890594872328195333  Reply to @lucasneal1 comment any other ideas i...   

      createTime                                        webVideoUrl  \
3060  1606642852  https://www.tiktok.com/@f1_flat_out/video/6900...   
4512  1601378772  https://www.tiktok.com/@noeldeyzel_bodybuilder...   
5535  1607518332  https://www.tiktok.com/@laykron/video/69042386...   
2144  1608269434  https://www.tiktok.com/@achi.roffazuid/video/6...   
1531  1604341686  https://www.tiktok.com/@bundaddy/video/6890594...   

                                               videoUrl videoUrlNoWaterMark  \
3060  https://v77.tiktokcdn.com/f6de29f3420e91622faf...                       
4512  https://v77.tiktokcdn.com/2a11914e741a065d1085...                       
5535  https://v77.tiktokcdn.com/8f0aaffcc42e40850132...                       
2144  https://v77.tiktokcdn.com/2f2e9c826f569f58fa12...                       
1531  https://v77.tiktokcdn.com/1bea1665140377dba7a6...                       

      diggCount  shareCount  playCount  commentCount  ...  \
3060      21700        1103     292500            78  ...   
4512      23200         514     332900           124  ...   
5535      28000        4533    2500000           668  ...   
2144      25200         194     439700           984  ...   
1531      20000         210     111100           466  ...   

                                         covers.default  \
3060  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
4512  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
5535  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
2144  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
1531  https://p16-sign-sg.tiktokcdn.com/obj/tos-mali...   

                                          covers.origin  \
3060  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
4512  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
5535  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
2144  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
1531  https://p16-sign-sg.tiktokcdn.com/obj/tos-mali...   

                                         covers.dynamic videoMeta.height  \
3060  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...             1024   
4512  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...              960   
5535  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...              960   
2144  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...             1024   
1531  https://p16-sign-sg.tiktokcdn.com/obj/tos-mali...             1024   

     videoMeta.width videoMeta.duration hashtags.id  hashtags.name  \
3060             576                 41       12573        redbull   
4512             540                 15       19093   bodybuilding   
5535             540                  9    49711363   рекомендации   
2144             576                 15    71559893         kesfet   
1531             576                 58      229207            fyp   

     hashtags.title hashtags.cover  
3060                                
4512                                
5535                                
2144                                
1531                                

[5 rows x 38 columns]

In [48]:
df_unique_videos

id                                               text  \
0     6907228749016714497                                  Confidence went 📈   
1     6875468410612993286  Quiet Zone... follow me on insta: joeysofo. Co...   
2     6898699405898059010  Iphone bend test🤗 #tiktok #viral #fyp #iphone ...   
8     6902819837345533186                                                      
9     6905635666588192002                           小技です👟✨#tiktok教室#tutorial   
...                   ...                                                ...   
5671  6877191692341054721                                #foryou #foryoupage   
5673  6908069845825359109  Stop eating 💩 #gttfg #gotothegym #swolefam #nu...   
5681  6883484287434378497                            #fy #foryoupage #foryou   
5684  6898721943978036481                     regretss 📈 #fyp #foryou #curls   
5687  6899116261746281730  The collab you didn’t know you needed, myself ...   

      createTime                                        webVideoUrl  \
0     1608214517  https://www.tiktok.com/@ninakleij/video/690722...   
1     1600819763  https://www.tiktok.com/@joeysofo/video/6875468...   
2     1606228625  https://www.tiktok.com/@jackeyephone/video/689...   
8     1607187987  https://www.tiktok.com/@naomivaneeren/video/69...   
9     1607843600  https://www.tiktok.com/@io.dreamer_mk/video/69...   
...          ...                                                ...   
5671  1601220970  https://www.tiktok.com/@artistmiranda/video/68...   
5673  1608410366  https://www.tiktok.com/@papaswolio/video/69080...   
5681  1602686079  https://www.tiktok.com/@sanaelfarah/video/6883...   
5684  1606233872  https://www.tiktok.com/@safae.kx/video/6898721...   
5687  1606325682  https://www.tiktok.com/@erinwilliams_1/video/6...   

                                               videoUrl videoUrlNoWaterMark  \
0     https://v77.tiktokcdn.com/ed1f811617d7b5e18b8d...                       
1     https://v77.tiktokcdn.com/ab935f1975cb8b69aebf...                       
2     https://v21.tiktokcdn.com/video/tos/alisg/tos-...                       
8     https://v21.tiktokcdn.com/video/tos/alisg/tos-...                       
9     https://v77.tiktokcdn.com/7622979a5ceb97c6da4e...                       
...                                                 ...                 ...   
5671  https://v77.tiktokcdn.com/12644d87ac40de1c1ab2...                       
5673  https://v77.tiktokcdn.com/740d0b0889f43900715c...                       
5681  https://v77.tiktokcdn.com/eed7b93664d2cfa5b122...                       
5684  https://v77.tiktokcdn.com/a402298fb8ed593ed456...                       
5687  https://v77.tiktokcdn.com/a6a5e4b4310213520be7...                       

      diggCount  shareCount  playCount  commentCount  ...  \
0          3710          50      44800            68  ...   
1         55700        1817     838100           936  ...   
2        936200       21100   15300000         27100  ...   
8         12900         197      94900           143  ...   
9          8805         198     115300            52  ...   
...         ...         ...        ...           ...  ...   
5671      13300         152     129300           111  ...   
5673      12200         223      80700           321  ...   
5681      26600        3392     449300           668  ...   
5684      10000         111      72200           274  ...   
5687      58900         235     309000           874  ...   

                                         covers.default  \
0     https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
1     https://p16-sign-sg.tiktokcdn.com/obj/tos-mali...   
2     https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
8     https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
9     https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
...                                                 ...   
5671  https://p16-sign-sg.tiktokcdn.com/obj/tos-alis...   
5673  https://p16-sign-sg.tiktokcdn.com/obj/tos-mali...

In [27]:
import pandas as pd
import os
from IPython.display import Video, display

# --- 1. Definisi Fungsi show_video ---
def show_video(file_path, width=None):
    """
    Menampilkan video di Jupyter Notebook.

    Args:
        file_path (str): Jalur (path) ke file video yang ingin ditampilkan.
                         Bisa berupa jalur relatif atau absolut.
    """
    if not os.path.exists(file_path):
        print(f"Error: File video tidak ditemukan di '{file_path}'")
        print("Pastikan nama file dan jalurnya sudah benar.")
        return

    print(f"Memutar video dari: {file_path}")
    try:
        video_player = Video(file_path, embed=True, width=width)
        display(video_player)
    except Exception as e:
        print(f"Gagal memutar video. Error: {e}")
        print("Pastikan format video kompatibel (misalnya .mp4 atau .webm).")


# --- 2. Persiapan Data (Jalankan ini di Cell yang sama) ---
# Anda bisa mengganti data dummy ini dengan data Anda sendiri.
data = {'desc': ['Video most like 1', 'Video most like 2', 'Video most like 3', 'Video most like 4', 'Video most like 5'],
        'diggCount_new': [21400, 21300, 27400, 24200, 21800],
        'video_path': [r'C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6899843622355750145.mp4', 
                       r'C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6904359798809054470.mp4', 
                       r'C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6895048600355704070.mp4',
                       r'C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6888373722546294022.mp4',
                       r'C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6901026135119760642.mp4'],
        'tiktok_music': ['https://sf77-sg.tiktokcdn.com/obj/tiktok-obj/6879039742646815489.mp3',
        'https://video-sg.tiktokv.com/storage/v1/tos-alisg-v-27dcd7/ba0786fecf35498cba4e259725c4e440?a=1233&br=250&bt=125&cd=0%7C0%7C0&cr=0&cs=&dr=0&ds=&er=0&l=202012211557500101890660493A124105&lr=default&mime_type=audio_mpeg&qs=6&rc=Mzs8NnltPDdkeDMzODU8M0ApOGRoOWU1ODxlN2k8aTtnOGc1LXAxMm1rYGxfLS1jMTRzczZjYDZeMl8zYDA2L2FfNjM6Yw%3D%3D&vl=&vr=&x-tos-algorithm=v2&x-tos-authkey=5bf25627da095a5cba28ace592de46cc&x-tos-expires=1608587884&x-tos-signature=Vd-e9LNcb4goa8hg-FnQ-R-KstM',
        'https://sf16-sg.tiktokcdn.com/obj/musically-maliva-obj/6878032546374929158.mp3',
        'https://sf16-sg.tiktokcdn.com/obj/tiktok-obj/17fd2400f9ae0386ad9a5c4c86bc7405.m4a',
        'https://sf77-sg.tiktokcdn.com/obj/musically-maliva-obj/6863594361750440710.mp3']}
df_path_videos = pd.DataFrame(data)

# Setelah menjalankan cell ini, fungsi show_video dan dataframe df_unique_videos sudah siap digunakan.
print("Persiapan selesai. Fungsi 'show_video' dan DataFrame 'df_unique_videos' sudah dimuat.")

Persiapan selesai. Fungsi 'show_video' dan DataFrame 'df_unique_videos' sudah dimuat.


In [28]:
df_path_videos

desc  diggCount_new  \
0  Video most like 1          21400   
1  Video most like 2          21300   
2  Video most like 3          27400   
3  Video most like 4          24200   
4  Video most like 5          21800   

                                          video_path  \
0  C:\Users\User\AppData\Roaming\Python\Python313...   
1  C:\Users\User\AppData\Roaming\Python\Python313...   
2  C:\Users\User\AppData\Roaming\Python\Python313...   
3  C:\Users\User\AppData\Roaming\Python\Python313...   
4  C:\Users\User\AppData\Roaming\Python\Python313...   

                                        tiktok_music  
0  https://sf77-sg.tiktokcdn.com/obj/tiktok-obj/6...  
1  https://video-sg.tiktokv.com/storage/v1/tos-al...  
2  https://sf16-sg.tiktokcdn.com/obj/musically-ma...  
3  https://sf16-sg.tiktokcdn.com/obj/tiktok-obj/1...  
4  https://sf77-sg.tiktokcdn.com/obj/musically-ma...

In [29]:
# --- Panggilan Fungsi show_video di Cell Baru ---
# Ini adalah bagian yang akan Anda jalankan secara terpisah.
try:
    # Cari video dengan 'like' terbanyak dari dataframe yang sudah dimuat
    random_video = df_path_videos.sample(n=1) # choose random videos to play
    video_popular_path = random_video['video_path'].iloc[0] # path to the videos directory

    # append tiktok music into videos
    music_append = random_video['tiktok_music'].iloc[0]

    # append the description from path is required
    description = random_video['desc'].iloc[0]

    # amount of likes
    likes_amount = random_video['diggCount_new'].iloc[0]

    # Ambil jalur file dari baris yang ditemukan
    print("Videos information random sample which popular was being filtered:")
    print(f"  Deskripsi: {description}")
    print(f"  Jumlah Likes: {likes_amount}")
    print(f"  Jalur File: {video_popular_path}")
    print(f"  Add tiktok music: {music_append}")

    # Panggil fungsi show_video dengan jalur yang sudah didapatkan
    show_video(video_popular_path, width=400)

except NameError:
    print("Error: DataFrame 'df_unique_videos' belum didefinisikan.")
    print("Pastikan Anda sudah menjalankan cell pertama terlebih dahulu.")
except KeyError:
    print("Error: Kolom 'diggCount' atau 'video_path' tidak ditemukan di dataframe.")
    print("Pastikan nama kolom sudah benar.")
except Exception as e:
    print(f"Terjadi kesalahan: {e}")

Videos information random sample which popular was being filtered:
  Deskripsi: Video most like 4
  Jumlah Likes: 24200
  Jalur File: C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6888373722546294022.mp4
  Add tiktok music: https://sf16-sg.tiktokcdn.com/obj/tiktok-obj/17fd2400f9ae0386ad9a5c4c86bc7405.m4a
Memutar video dari: C:\Users\User\AppData\Roaming\Python\Python313\site-packages\ML-Production\Tiktok-ML\Videos\6888373722546294022.mp4


Tiktok Analytics Playcount For Data Science

In [30]:
# set bucket ranges
buckets = list(range(0, 25000000, 500000)) # range like around 

plays = df_unique_videos.groupby(my_cut(df_unique_videos['playCount'], buckets, upper_infinite=True)).playCount.count()
likes = df_unique_videos.groupby(my_cut(df_unique_videos['diggCount'], buckets, upper_infinite=True)).diggCount.count()

# Transform from series to dataframe with some small modifications
plays = plays.rename('plays').to_frame().reset_index()
likes = likes.rename('likes').to_frame().reset_index()

# create subplots, two rows and 1 column each row
fig = make_subplots(2, 1, subplot_titles=("Distribution of Plays", "Distribution of Likes"))

# First plot
fig.add_trace(
    go.Bar(y = plays['playCount'], 
           x = plays['plays'], 
           name="Plays",
           text = plays['plays'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='rgb(162, 210, 255)'
    ),
    row=1,col=1
)

# second plot
fig.add_trace(
    go.Bar(y = likes['diggCount'], 
           x = likes['likes'], 
           name="Likes",
           text = likes['likes'], 
           orientation='h',
           texttemplate='%{text:.2s}', 
           textposition='outside', 
           marker_color='black'
    ),
    row=2,col=1
)

fig.update_layout(uniformtext_minsize=8,
                  uniformtext_mode='hide',
                  title_text="Multiple Subplots with Titles",
                  height=1200,
                  template='plotly_white',
                  margin=go.layout.Margin(
                      l=130, r=5, b=5, t=100, pad=10
                  ))

fig.update_xaxes(title_text='Videos')
fig.update_yaxes(title_text='Plays', col=1, row=1, automargin=False)
fig.update_yaxes(title_text='Likes', col=1, row=2, automargin=False)
fig.show(config={'displayModeBar': False})

In [31]:
# Focus on dataset from 0 till 50.000 likes
df_videos_users_focus = df_unique_videos[df_unique_videos['playCount'] <= 2500000] # count of dataset likes

# Create a scatter plot with a trendline
fig = px.scatter(df_videos_users_focus, trendline='ols',
                 x='playCount',
                 y='diggCount',
                 labels={
                     'playCount':'Plays',
                     'diggCount':'Likes'
                 },
                 log_y=True,
                 trendline_color_override="#ff7096",
                 template='plotly_white')

fig.update_traces(marker=dict(
    color='#4cc9f0',
    opacity=0.6
))
fig.show()

In [32]:
# Create a DataFrame of the data
df_plays = pd.DataFrame(trending_videos_list) # containing data from trending video list into dataframe

# Let's expand the hashtag cell containing dictionaries to columns
df_plays = df_plays.explode('playCount')

# Expand certain cells containing dictionaries to columns
df_plays = df_plays.apply(object_to_columns, playCount='plays', axis=1)
plays = df_plays[['playCount']].copy().dropna()
plays.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1000 entries, 0 to 999
Data columns (total 1 columns):
 #   Column     Non-Null Count  Dtype
---  ------     --------------  -----
 0   playCount  1000 non-null   int64
dtypes: int64(1)
memory usage: 15.6 KB


In [34]:
# Add column with default value
plays['count'] = 1

# Count all hashtags, group and replace the count column value with the sum
plays = plays.groupby(['playCount'])['count'].count().reset_index()

# Sort by most popular hashtags and keep the top 15
plays = plays.sort_values(by='count', ascending=False)[:4] # analysis data based on amount of data we want to choose

# Create a Pie Chart with all values
fig = go.Figure(data=[go.Pie(
    labels=plays['playCount'],
    values=plays['count'],
    textinfo='label+percent',
    insidetextorientation='radial'
)],
# Set colours for layout
layout={'colorway': ["#f72585","#b5179e",
                     "#7209b7","#560bad",
                     "#480ca8","#3a0ca3",
                     "#3f37c9","#4361ee",
                     "#4895ef","#4cc9f0"]})

fig.update_layout(title_text="Tiktok plays trending analytics",
                  height=700,
                  width=800,
                  margin=go.layout.Margin(
                      l=130, r=5, b=5, t=100, pad=10))
fig.show(config={'displayModeBar': False})